In [1]:
import pandas as pd
import numpy as np
from statsmodels.tsa.stattools import acf, pacf
import quandl
import plotly
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [2]:
def createRandomDataFeed(n_samples, corr, mu=0, annual_sigma=.15, start_value=1000):
    """

    :param n_samples: number of sample length
    :param corr: autocorrelation coefficent should be between 0 and 1
    :param mu: mean of the distribution
    :param annual_sigma: std dev of distribution
    :return: pd.DF col['close']
    """
    assert 0 < corr < 1, "Auto-correlation must be between 0 and 1"

    # Find out the offset `c` and the std of the white noise `sigma_e`
    # that produce a signal with the desired mean and variance.
    # See https://en.wikipedia.org/wiki/Autoregressive_model
    # under section "Example: An AR(1) process".

    sigma = annual_sigma / np.sqrt(365)

    c = mu * (1 - corr)
    sigma_e = np.sqrt((sigma ** 2) * (1 - corr ** 2))

    # Sample the auto-regressive process.
    signal = [c + np.random.normal(0, sigma_e)]
    for _ in range(1, n_samples):
        signal.append(c + corr * signal[-1] + np.random.normal(0, sigma_e))

    # create the price index
    rets = signal
    price = [start_value]
    for i in np.arange(len(rets)):
        price.append(price[-1] * rets[i] + price[-1])

    # create the data frame
    price = pd.DataFrame(price)
    price.columns = ['close']

    start_date = pd.to_datetime('01-01-1900')
    price.index = pd.date_range(start=start_date, end=start_date + pd.DateOffset(days=len(signal)))
    return price

def compute_corr_lag_1(signal):
    return np.corrcoef(signal[:-1], signal[1:])[0][1]

Functionalize and replicate

In [3]:
def MCSimulatedData(n_samples, corr, mu=0, annual_sigma=.15, stopMult=3,
                    start_value=1000, n_runs=1, rng=np.random.default_rng(12345)):
    """
    to generate an autocorrelated return index which creates a price index. Then apply a stoploss rule and 
    extract the trade values

    :param n_samples: int- how long for the generated return series
    :param corr - float 0<i<1 correlation coefficent to generate
    :param stopMult - int - how many std dev of price to use as a stop
    :param mu - float the mean of the series
    :param annual_sigma - float annualize standard deviation
    :param start_value - int- starting value of the instrument
    :param n_runs - int how many montecarlo runs to run
    :param rng - numpy random number generator with seed
    """
    # create new pos object in namespace
    newPosition = {'direction': None, 'entryPx': np.nan,
                   'entryDate': None, 'exitPx': np.nan,
                   'stopDist': np.nan, 'stopPx': np.nan,
                   'exitDate': None, 'open': True}

    # store the run of Positions
    totalPos = []

    for run in range(n_runs):
        # create the original random data
        data = createRandomDataFeed(n_samples=15000, corr=.15, mu=0)
        # calculate returns and std dev
        data['returns'] = data.close.pct_change()
        data['stdDevPx'] = data.close.rolling(window=30).std()
        data.dropna(inplace=True)

        # create a list of trade positions
        posList = []

        # prime the list by randomly generating a entry for the first day
        if rng.random() >= .50:
            addPos = newPosition.copy()
            addPos.update(dict(direction=1, entryPx=data.iloc['01-30-1900', 'close'],
                               entryDate=data.index[0], stopDist=stopMult * data.loc['01-30-1900', 'stdDevPx']))
            addPos['stopPx'] = addPos['entryPx'] - addPos['stopDist']
            posList.append(addPos)
        else:
            addPos = newPosition.copy()
            addPos.update(dict(direction=-1, entryPx=data.loc['01-30-1900', 'close'], entryDate=data.index[0],
                               stopDist=stopMult * data.loc['01-30-1900', 'stdDevPx']))
            addPos['stopPx'] = addPos['entryPx'] + addPos['stopDist']
            posList.append(addPos)

        # prime the close incrementers
        highestClose = 0
        lowestClose = 100000
        # do the forloop backtest
        for row in data.iterrows():
            # track the high/low closes
            if highestClose < row[1]['close']:
                highestClose = row[1]['close']
            if lowestClose > row[1]['close']:
                lowestClose = row[1]['close']
            if posList[-1]['open'] and posList[-1]['direction'] == 1:
                # update the stop
                if posList[-1]['stopPx'] < (row[1]['close'] - posList[-1]['stopDist']):
                    posList[-1]['stopPx'] = (row[1]
                                             ['close'] - posList[-1]['stopDist'])

                # we are long
                if posList[-1]['stopPx'] >= row[1]['close']:
                    posList[-1]['exitPx'] = row[1]['close']
                    posList[-1]['exitDate'] = row[0]
                    posList[-1]['open'] = False
            elif posList[-1]['open'] and posList[-1]['direction'] == -1:
                # update the stop
                if posList[-1]['stopPx'] > (row[1]['close'] + posList[-1]['stopDist']):
                    posList[-1]['stopPx'] = (row[1]
                                             ['close'] + posList[-1]['stopDist'])

                # we are short
                if posList[-1]['stopPx'] <= row[1]['close']:
                    posList[-1]['exitPx'] = row[1]['close']
                    posList[-1]['exitDate'] = row[0]
                    posList[-1]['open'] = False
            elif posList[-1]['open'] == False:
                # reset highest lowest closes
                highestClose = 0
                lowestClose = 100000
                # position is closed add another
                if rng.random() >= .50:
                    addPos = newPosition.copy()
                    addPos.update(dict(direction=1, entryPx=row[1]['close'],
                                       entryDate=row[0], stopDist=stopMult * row[1]['stdDevPx']))
                    addPos['stopPx'] = addPos['entryPx'] - addPos['stopDist']
                    posList.append(addPos)
                else:
                    addPos = newPosition.copy()
                    addPos.update(dict(direction=-1, entryPx=row[1]['close'],
                                       entryDate=row[0], stopDist=stopMult * row[1]['stdDevPx']))
                    addPos['stopPx'] = addPos['entryPx'] + addPos['stopDist']
                    posList.append(addPos)

        # add it to the total list
        totalPos.extend(posList)

        return pd.DataFrame(totalPos).dropna()

In [4]:
def calcPNL(row):
    if row['direction'] == 1:
        return row['exitPx'] - row['entryPx']
    else:
        return row['entryPx'] - row['exitPx']

In [5]:
mcResults = {}

for corrValue in range(0, 35, 5):
    for stopMulvalue in range(1, 11, 1):
        for volVal in range(0, 55, 5):
            mcResults[(corrValue/100, stopMulvalue, volVal/100)] = MCSimulatedData(n_samples=15000, corr=corrValue/100, mu=0, annual_sigma=volVal/100, 
                                                                                  stopMult=stopMulvalue, start_value=1000, n_runs=1500, 
                                                                                  rng = np.random.default_rng(12345))


In [6]:
tradeStats = []
for k, v in mcResults.items():
    if v.empty:
            tradeStats.append({"corr": k[0], "stop": k[1], 'annVol':k[2],
                               'avgTrade':np.nan, 'avgWin': np.nan, 
                               'avgLoss':np.nan})
    else:
        v.loc[:, 'PnL'] = v.apply(calcPNL, axis=1)
        tradeStats.append({"corr": k[0], "stop": k[1], 'annVol':k[2],
                       'avgTrade':v['PnL'].mean(), 'avgWin': v[v['PnL']>0]['PnL'].mean(), 
                       'avgLoss':v[v['PnL']<0]['PnL'].mean()})

Sample trade numbers

In [7]:
tradeNumbers = []
for k, v in mcResults.items():
    tradeNumbers.append(len(v))

In [8]:
tradeNumbers = np.array(tradeNumbers)

In [9]:
np.mean(tradeNumbers)

218.74805194805194

In [10]:
np.max(tradeNumbers)

1332

In [11]:
np.sum(tradeNumbers)

168436

In [12]:
tradeStats = pd.DataFrame(tradeStats)
tradeStats

corr  stop  annVol    avgTrade      avgWin     avgLoss
0     0.0     1    0.00    1.271714   33.632440  -19.056903
1     0.0     1    0.05    1.291697   21.946484  -11.549242
2     0.0     1    0.10    2.230963   37.148018  -19.242805
3     0.0     1    0.15    0.892809    9.116884   -4.460275
4     0.0     1    0.20    1.239378   13.236820   -6.930554
..    ...   ...     ...         ...         ...         ...
765   0.3    10    0.30  -75.691608  159.565321 -118.465595
766   0.3    10    0.35 -114.714019  289.529227 -215.774831
767   0.3    10    0.40 -118.710318   78.448539 -197.573861
768   0.3    10    0.45  -86.198290   88.286833 -139.886020
769   0.3    10    0.50 -113.313412         NaN -113.313412

[770 rows x 6 columns]

In [13]:
tradeStats['WLRatio'] = tradeStats['avgWin']/abs(tradeStats['avgLoss'])

In [14]:
tradeStats['WLRatio'].mean()

1.732786764613738

In [15]:
tradeStats['WLRatio'].min()

0.049606538097132606

In [16]:
tradeStats['WLRatio'].max()

5.910743942129242

In [17]:
tradeStats['avgTrade'].mean()

-6.120795742989892

Hypo 1: trailing stop provides edge

In [42]:
tradeStats.loc[:,'avgTrade'].mean()

-6.120795742989892

In [43]:
avgTrade_corr = tradeStats.loc[:,['corr', 'avgTrade', 'WLRatio']].groupby('corr').mean()
avgTrade_corr

avgTrade   WLRatio
corr                     
0.00 -11.032088  1.700114
0.05  -8.793927  1.700080
0.10   1.662855  1.798031
0.15  -6.876494  1.759866
0.20  -7.068911  1.711757
0.25  -8.104173  1.645382
0.30  -2.632832  1.812383

In [46]:
fig = go.Figure(data=[go.Bar(x=avgTrade_corr.index, y=avgTrade_corr['avgTrade'])])
fig.update_layout(
    xaxis_title="AutoCorrelation Factor",
    yaxis_title="Average Trade",
)
fig.show()

Hypo 2 Trailing stops alter trade stats  
Plot average win loss ratio over 3 sets of stop values 1 5 and 10

In [47]:
tradeStats.loc[:,'WLRatio'].mean()

1.732786764613738

In [18]:
tradeStats[tradeStats['stop']==1].pivot(index='corr', values='WLRatio', columns='annVol')

annVol      0.00      0.05      0.10      0.15      0.20      0.25      0.30  \
corr                                                                           
0.00    1.764843  1.900253  1.930489  2.044019  1.909922  2.145472  1.926959   
0.05    1.904568  2.061627  1.783380  1.819147  2.006905  1.858086  1.937809   
0.10    2.008818  1.786491  1.931328  2.169993  2.041139  2.018891  1.936455   
0.15    1.877556  2.023983  1.861356  2.136997  1.946679  1.970311  2.001609   
0.20    1.874816  1.582111  1.835946  1.991529  1.856495  2.114974  1.851812   
0.25    2.116980  1.768847  2.138613  2.086717  1.711830  1.994832  1.899161   
0.30    2.039171  1.963208  1.811012  1.868441  1.866511  1.826292  2.075429   

annVol      0.35      0.40      0.45      0.50  
corr                                            
0.00    1.997484  2.026337  1.866913  2.016542  
0.05    2.120484  1.979358  2.138554  2.232596  
0.10    1.993123  1.825245  1.848141  1.910962  
0.15    2.012112  1.921671  1.759982  2.194523  
0.20    1.781754  1.998714  1.776703  1.920218  
0.25    1.895982  1.751388  2.019846  1.854232  
0.30    1.791420  1.987833  2.116836  1.908890

In [120]:
fig = go.Figure(data=[go.Surface(z=tradeStats[tradeStats['stop']==10].pivot(index='corr', values='WLRatio', columns='annVol'), 
                                 x=tradeStats[tradeStats['stop']==10].pivot(index='corr', values='WLRatio', columns='annVol').index, 
                                 y=tradeStats[tradeStats['stop']==10].pivot(index='corr', values='WLRatio', columns='annVol').columns,
                                contours={"z": {"show": True, "start": 1, "end": 1.1, "size":1}},
                                  cmin=0, cmax=5)])

fig.update_layout(
        scene = {
            "xaxis": {"nticks": 10},
            "zaxis": {"nticks": 10},
            'yaxis': {"nticks":10},
            "aspectratio": {"x": 1, "y": 1, "z": .5},
             "xaxis_title":'AutoCorrelation Value',
             "yaxis_title":'Annualized Volatility',
             "zaxis_title":'Win Loss Ratio'},
                    
            width= 900,
            margin=dict(r=20, b=10, l=10, t=10)
        )

fig.show()

In [114]:
extractPnL = np.array([])

for k,v in mcResults.items():
    extractPnL= np.append(extractPnL, v.PnL.values)

In [77]:
len(extractPnL)

168436

In [119]:
fig =go.Figure(go.Box(y=extractPnL, name="Trade PnL"))
fig.show()

In [76]:
from scipy.stats import skew
skew(extractPnL)

6.547853443923475

Volatility vs Trailing Stop vs Avg Trade


In [79]:
tradeStats.pivot(index='stop', values='avgTrade', columns='annVol', aggfunc='mean')

TypeError: pivot() got an unexpected keyword argument 'aggfunc'

In [82]:
volStopPivot = pd.pivot_table(tradeStats,index='stop', values='avgTrade', columns='annVol', aggfunc='mean')
volStopPivot

annVol       0.00       0.05       0.10       0.15       0.20       0.25  \
stop                                                                       
1        3.477889   1.526928   1.611856   1.978852   1.431213   2.718601   
2        3.147156   2.240856   2.488847   3.259975   2.064389   3.749855   
3        5.228372   2.395660   4.776709   0.771318  -2.653259  -1.653345   
4        8.267844  -3.609883  -1.842047   8.178230  -0.670993   1.825811   
5       11.659204   4.769302  -1.418248  -7.293599   9.944876   0.251136   
6       19.636038   6.470366   8.209242 -13.524030 -12.340456 -32.478505   
7      -15.490751 -16.514500   2.735887 -23.329246  -3.814917  33.655012   
8       -9.224806 -22.588671   1.049866 -20.708251 -12.977616 -12.560208   
9       -2.230117  -9.037681 -21.713776 -45.303587 -26.953397  26.339097   
10     -47.356997   2.199461 -41.690986 -92.897768 -60.806107  15.207601   

annVol       0.30       0.35       0.40       0.45       0.50  
stop                                                           
1        3.051446   5.117863   1.118666   1.222514   2.368735  
2        3.076119   0.810381   0.695957   2.362592   6.562303  
3        0.180556   1.109997   3.126009  -2.047543   2.359807  
4       -0.071910   6.396215   3.036381   9.960444   5.070855  
5       -1.373135 -14.793900   9.355970   0.530834   1.599356  
6       -1.115717 -15.726777 -12.857706   3.694856  41.342116  
7       -5.613235  -6.950649  -0.266772  -8.255228  10.835707  
8        4.399428 -35.971358  -2.123580  28.610878  -0.106711  
9      -31.528152 -28.121896 -38.511194  -9.063507 -18.556452  
10     -98.478124 -64.257342 -65.522788   5.390766 -15.944313

In [94]:
fig = go.Figure(data=[go.Surface(z=volStopPivot, 
                                 x=volStopPivot.index, 
                                 y=volStopPivot.columns,
                                contours={"z": {"show": True, "start": 0, "end": 0.1, "size":1}})])

fig.update_layout(scene = dict(
                    xaxis_title='Stop Multiplier Value',
                    yaxis_title='Annualized Volatility',
                    zaxis_title='Mean of Average Trade'),
                    width= 900,
                    margin=dict(r=20, b=10, l=10, t=10))

fig.show()

In [122]:
volStopPivot = pd.pivot_table(tradeStats,index='stop', values='avgTrade', columns='corr', aggfunc='mean')

In [125]:
fig = go.Figure(data=[go.Surface(z=volStopPivot, 
                                 x=volStopPivot.index, 
                                 y=volStopPivot.columns,
                                contours={"z": {"show": True, "start": 0, "end": 0.1, "size":1}})])

fig.update_layout(scene = dict(
                    xaxis_title='Stop Multiplier Value',
                    yaxis_title='AutoCorrelation',
                    zaxis_title='Mean of Average Trade'),
                    width= 900,
                    margin=dict(r=20, b=10, l=10, t=10))

fig.show()

In [124]:
volStopPivot

corr       0.00       0.05       0.10       0.15       0.20       0.25  \
stop                                                                     
1      1.893707   3.590994   2.194916   1.990578   3.635089   1.198481   
2      6.697959   1.226127   1.176083   2.292135   2.901209   2.868707   
3      0.372330   1.053760   0.008515  -0.932700   3.161466  -2.152272   
4      3.075578   6.028422   4.119816   1.772767   4.505366   2.839419   
5     -2.248088   4.804408   9.513265   0.022189   5.686765  -6.628257   
6    -20.698126  17.852519  12.639804 -11.635055 -11.893022   7.193490   
7    -16.578067 -16.205153   2.518670  -7.047490  -7.111098  12.595015   
8    -13.799592 -15.326270  10.401662  -9.190446 -24.303823  -4.810163   
9    -37.500139 -45.135670   8.199890  -9.684534 -10.690091 -22.178287   
10   -31.536441 -45.828405 -34.144075 -36.352384 -36.580973 -71.967865   

corr       0.30  
stop             
1      1.802775  
2      2.220418  
3      7.139809  
4      0.911962  
5     -2.730049  
6      1.010027  
7     10.822591  
8      4.718886  
9    -13.262497  
10   -38.962238